# 0. 라이브러리 불러오기

In [0]:
%pip install sqlalchemy psycopg2-binary

Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.
Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.


In [0]:
dbutils.library.restartPython()

In [0]:
import pandas as pd
import psycopg2
from sqlalchemy import create_engine, text
import numpy as np

# 1. 데이터 불러오기 (DB - Spark DataFrame)

## 1) JDBC 방식

In [0]:
jdbc_user = "postgres"
jdbc_pass = "asdASD123!@#"
host = "cloud-postgredb-server.postgres.database.azure.com"
port = "5432"
jdbc_url = f"jdbc:postgresql://{host}:{port}/postgres"

# silver 스키마의 특정 테이블 읽기
df = (spark.read.format("jdbc")
      .option("url", jdbc_url)
      .option("dbtable", "silver.slv_career_js_posting_company")     # ← 스키마.테이블
      .option("user", jdbc_user)
      .option("password", jdbc_pass)
      .option("driver", "org.postgresql.Driver")
      # 성능 (선택): 파티션 컬럼/범위 지정
      # .option("partitionColumn","id").option("lowerBound","1").option("upperBound","1000000").option("numPartitions","8")
      .load())

---------------------------------------------------------------------------
Py4JJavaError                             Traceback (most recent call last)
File <command-4866686860066942>, line 15
      5 jdbc_url = f"jdbc:postgresql://{host}:{port}/postgres"
      7 # silver 스키마의 특정 테이블 읽기
      8 df = (spark.read.format("jdbc")
      9       .option("url", jdbc_url)
     10       .option("dbtable", "silver.slv_career_js_posting_company")     # ← 스키마.테이블
     11       .option("user", jdbc_user)
     12       .option("password", jdbc_pass)
     13       # 성능 (선택): 파티션 컬럼/범위 지정
     14       # .option("partitionColumn","id").option("lowerBound","1").option("upperBound","1000000").option("numPartitions","8")
---> 15       .load())

File /databricks/spark/python/pyspark/instrumentation_utils.py:47, in _wrap_function.<locals>.wrapper(*args, **kwargs)
     45 start = time.perf_counter()
     46 try:
---> 47     res = func(*args, **kwargs)
     48     logger.log_success(
     49         module_n

In [0]:
q_tables = """
( SELECT table_schema, table_name
  FROM information_schema.tables
  WHERE table_type='BASE TABLE'
  ORDER BY table_schema, table_name
) t
"""
df_list = (spark.read.format("jdbc")
  .option("url", jdbc_url)
  .option("dbtable", q_tables)
  .option("user", jdbc_user)
  .option("password", jdbc_pass)
  .option("driver", "org.postgresql.Driver")
  .load())
df_list.show(200, truncate=False)

+------------------+--------------------------+
|table_schema      |table_name                |
+------------------+--------------------------+
|bronze            |brz_employee_info         |
|bronze            |brz_hf_community          |
|bronze            |brz_hf_files              |
|bronze            |brz_hf_meta               |
|bronze            |brz_jumpit_company        |
|bronze            |brz_jumpit_job_category   |
|bronze            |brz_jumpit_posting        |
|bronze            |brz_saramin_company       |
|bronze            |brz_saramin_company_salary|
|bronze            |brz_saramin_posting       |
|information_schema|sql_features              |
|information_schema|sql_implementation_info   |
|information_schema|sql_parts                 |
|information_schema|sql_sizing                |
|pg_catalog        |pg_aggregate              |
|pg_catalog        |pg_am                     |
|pg_catalog        |pg_amop                   |
|pg_catalog        |pg_amproc           

## 2) psycopg2-binary 방식

In [0]:
conn = psycopg2.connect(
    host="cloud-postgredb-server.postgres.database.azure.com",
    port="5432",
    database="postgres",
    user="Drawbridge",
    password="asdASD123!@#"
)

df = pd.read_sql("SELECT * FROM silver.slv_career_js_posting_company;", conn)

conn.close()

/root/.ipykernel/10334/command-5514411694865043-1455951629:9: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df = pd.read_sql("SELECT * FROM silver.slv_career_js_posting_company;", conn)


In [0]:
display(df)

posting_id posting_title_j posting_title_s company_name_j company_name_s company_name_clean_j company_name_clean_s job_category job_category_kor posting_tech_stack experience_j experience_s education_j education_s employment_type salary position company_keywords_jumpit company_tech_stack company_type industry start_datetime end_datetime posting_views_total applicants_total exp_min exp_max edu_category 51746001 3D Scanning Application 개발(for iPad) 3D Scanning Application 개발(for iPad) 메디트 (주)메디트 메디트 메디트 1 서버/백엔드 개발자 SwiftUI;Xcode;vscode.dev 경력 1~10년 경력 1~10년 대학교졸업(4년) 이상 대졸(4년제) 이상 정규직 회사내규에 따름 연봉상승률 10% 이상;평균연봉 상위 10%;급성장중;장기근속 포상;MBK파트너스 계열사;매출액 1000억 기업;9호선 역세권 기업;유연근무제;평균연봉 7,000 이상 C#;AI/인공지능;Qt;Xcode;Babel;CMake;DeepLearning;Spark Framework;Windows;iOS;rollup;TypeScript;QA;Backendless;REST API;JavaScript;TCP/IP;Productboard;Embedded;vscode.dev;macOS;Flask;WebGL;Java;CSS 3;C++;Mac OS X;SW;AWS CloudTrail;Google Cloud Platform;OpenGL;Embedded Linux;SwiftUI;Vite;React;WebSocket;CUDA;Vue.js;Git;Linux;React D3 Library;HTML5;Spring Framework;Transformers;FastAPI;Swift;Webpack 중견기업;주식회사;병역특례 인증업체;수출입 기업 기타 주변기기 제조업 2025.09.06 00:00 2025.10.05 23:59 39.0 null 1 10 대졸(예정) 51746001 3D Scanning Application 개발(for iPad) 3D Scanning Application 개발(for iPad) 메디트 (주)메디트 메디트 메디트 3 웹 풀스택 개발자 SwiftUI;Xcode;vscode.dev 경력 1~10년 경력 1~10년 대학교졸업(4년) 이상 대졸(4년제) 이상 정규직 회사내규에 따름 연봉상승률 10% 이상;평균연봉 상위 10%;급성장중;장기근속 포상;MBK파트너스 계열사;매출액 1000억 기업;9호선 역세권 기업;유연근무제;평균연봉 7,000 이상 C#;AI/인공지능;Qt;Xcode;Babel;CMake;DeepLearning;Spark Framework;Windows;iOS;rollup;TypeScript;QA;Backendless;REST API;JavaScript;TCP/IP;Productboard;Embedded;vscode.dev;macOS;Flask;WebGL;Java;CSS 3;C++;Mac OS X;SW;AWS CloudTrail;Google Cloud Platform;OpenGL;Embedded Linux;SwiftUI;Vite;React;WebSocket;CUDA;Vue.js;Git;Linux;React D3 Library;HTML5;Spring Framework;Transformers;FastAPI;Swift;Webpack 중견기업;주식회사;병역특례 인증업체;수출입 기업 기타 주변기기 제조업 2025.09.06 00:00 2025.10.05 23:59 39.0 null 1 10 대졸(예정) 51704621 AI Artist / Software Engineer / Full Stack AI Artist / Software Engineer / Full Stack 블루개러지 (주)블루개러지 블루개러지 블루개러지 1 서버/백엔드 개발자 AWS;GCP 경력 3~15년 경력 3~15년 무관 학력무관 정규직 면접 후 결정 연봉상승률 20% 이상;매출액 500억 기업;급성장중;제이와이피엔터테인먼트 계열사;5호선 역세권 기업;유연근무제;매출액 20% 지속성장;평균연봉 6,000 이상 PostgreSQL;OpenGL;GraphQL;GraphicsMagick;React;Linear;Vulkan;TypeScript;PyTorch;GCP;Django;MySQL;3D Rendering;Pandas;React Native;AWS;Python 중소기업 그 외 기타 상품 전문 도매업 2025.09.01 00:00 2025.09.30 23:59 38.0 2.0 3 15 고졸 미만;고졸(예정);초대졸(예정);대졸(예정);석박사(예정) 51704621 AI Artist / Software Engineer / Full Stack AI Artist / Software Engineer / Full Stack 블루개러지 (주)블루개러지 블루개러지 블루개러지 2 프론트엔드 개발자 AWS;GCP 경력 3~15년 경력 3~15년 무관 학력무관 정규직 면접 후 결정 연봉상승률 20% 이상;매출액 500억 기업;급성장중;제이와이피엔터테인먼트 계열사;5호선 역세권 기업;유연근무제;매출액 20% 지속성장;평균연봉 6,000 이상 PostgreSQL;OpenGL;GraphQL;GraphicsMagick;React;Linear;Vulkan;TypeScript;PyTorch;GCP;Django;MySQL;3D Rendering;Pandas;React Native;AWS;Python 중소기업 그 외 기타 상품 전문 도매업 2025.09.01 00:00 2025.09.30 23:59 38.0 2.0 3 15 고졸 미만;고졸(예정);초대졸(예정);대졸(예정);석박사(예정) 51768990 Backend 개발자 Backend 개발자 스마트푸드네트웍스 스마트푸드네트웍스(주) 스마트푸드네트웍스 스마트푸드네트웍스 1 서버/백엔드 개발자 Java;Kotlin;Spring;QueryDSL;AWS;Git;Jira;Confluence 경력 5~15년 경력 5~15년 무관 학력무관 정규직 회사내규에 따름 연봉상승률 10% 이상;급성장중;자유로운 연차;3호선 역세권 기업;평균연봉 6,000 이상 Java;QueryDSL;Next.js;Spring;Jira;SQL;Kotlin;pnpm;React Query;Jotai;TypeScript;R;Git;Confluence;TailwindCSS;AWS;Webpack;Python 중견기업;주식회사 화물운송 중개, 대리 및 관련 서비스업 2025.09.08 00:00 2025.10.07 23:59 114.0 25.0 5 15 고졸 미만;고졸(예정);초대졸(예정);대졸(예정);석박사(예정) 51583665 백엔드 경력 채용 (6~9년) 백엔드 경력 채용 (6~9년) 텐빌리언 텐빌리언 텐빌리언 텐빌리언 1 서버/백엔드 개발자 Git;SpringBoot;DB 경력 6~9년 경력 6~9년 대학교졸업(4년) 이상 대졸(4년제) 이상 정규직 면접 후 결정 장기근속 포상;자유로운 연차;점심지원 CSS 3;Spring Boot;iOS;React;REST API;jQuery;Git;HTML5;JavaScript;Network;PHP;Flutter;Android OS;AWS;DB 쇼핑몰·오픈마켓 2025.08.18 00:00 2025.09.16 23:59 170.0 2.0 6 9 대졸(예정) 51692814 시니어 백엔드 개발자(5년 이상) 시니어 백엔드 개발자(5년 이상) 더스윙 (주)더스윙 더스윙 더스윙 1 서버/백엔드 개발자 SpringBoot;SpringDataJPA;Java;Kotlin 경력 5~15년 경력 5~15년 대학교졸업(4년) 이상 대졸(4년제) 이상 정규직 회사내규에 따름 연봉상승률 20% 이상;매출액 500

# 2. 전처리

require_experience_single_year (정수 0–20) : 하한가중 분위수+상한 캡으로 만든 단일 연차

require_experience_role : 신입/사원/대리/과장/차·부장 (국내 다수결 경계)

posting_tech_stack_one : 세미콜론 분리 후 trim/explode한 단일 스택명

posting_count_s : (연차×직급×스택×직군×월) 별 posting_id countDistinct

job_category_kor : 직군

require_experience_band_kr (옵션) : 트렌드용 밴드(신입,1–3,3–5,5–10,10+)

posting_start_month_key (옵션) : yyyymm (시계열 축)

require_experience_sigle_year : 요청 이름 호환(오타 별칭)

In [0]:
#df.createOrReplaceTempView("src")
spark.createDataFrame(df).createOrReplaceTempView("src")

In [0]:
from pyspark.sql import functions as F, types as T, Window as W
import re

# ============ 0) 상수/유틸 ============
Y_MAX = 20.0
CAP_K = 6.0

# 카테고리 기본 우선순위(특화 > 일반) : 대표 카테고리 선정에 사용
# 가장 일반적인 sw/솔루션, 웹풀스택개발자에만 +3 주고, 나머지는 모두 동일하게 10으로 두겠음.
base_priority = [
    ("안드로이드 개발자",     10),
    ("iOS 개발자",          10),
    ("크로스플랫폼 앱개발자", 10),
    ("게임 서버 개발자",     10),
    ("게임 클라이언트 개발자", 10),
    ("VR/AR/3D",           10),
    ("DBA",                10),
    ("DevOps/시스템 엔지니어", 10),
    ("정보보안 담당자",      10),
    ("QA 엔지니어",         10),
    ("HW/임베디드",        10),
    ("빅데이터 엔지니어",    10),
    ("인공지능/머신러닝",    10),
    ("블록체인",            10),
    ("프론트엔드 개발자",    10),
    ("서버/백엔드 개발자",   10),
    ("기술지원",            10),
    ("웹퍼블리셔",          10),
    ("SW/솔루션",           13),
    ("개발 PM",            10),
    ("웹 풀스택 개발자",      13)
]

# base_priority = [
#     ("안드로이드 개발자",     30),
#     ("iOS 개발자",          30),
#     ("크로스플랫폼 앱개발자", 29),
#     ("게임 서버 개발자",     28),
#     ("게임 클라이언트 개발자", 28),
#     ("VR/AR/3D",           27),
#     ("DBA",                26),
#     ("DevOps/시스템 엔지니어", 26),
#     ("정보보안 담당자",      25),
#     ("QA 엔지니어",         24),
#     ("HW/임베디드",         24),
#     ("빅데이터 엔지니어",    23),
#     ("인공지능/머신러닝",    23),
#     ("블록체인",            22),
#     ("프론트엔드 개발자",    15),
#     ("서버/백엔드 개발자",   15),
#     ("기술지원",            14),
#     ("웹퍼블리셔",          14),
#     ("SW/솔루션",           13),
#     ("개발 PM",            13),
#     ("웹 풀스택 개발자",      5)  # 가장 일반
# ]
schema = T.StructType([
    T.StructField("job_category_kor", T.StringType(), False),
    T.StructField("base_pri", T.IntegerType(), False),
])
cat_pri_df = spark.createDataFrame(base_priority, schema)

# 제목 키워드(대표카테고리 점수 보정)
cat_title_patterns = {
    "서버/백엔드 개발자": r"(백엔드|서버|server|backend|스프링\s*부트|spring\s*boot|노드\.?js|node\.?js|익스프레스|express|장고|django|fast\s*api|fastapi|고랭|고언어|golang|go\b|gRPC|grpc|REST\s*API|msa|마이크로서비스)",
    "프론트엔드 개발자": r"(프론트|프론트엔드|웹\s*프론트|frontend|리액트|react|뷰|vue|앵귤러|angular|스벨트|svelte|타입스크립트|typescript|넥스트\.?js|next\.?js|눅스트\.?js|nuxt\.?js|웹팩|webpack|바이트|vite)",
    "웹 풀스택 개발자": r"(풀\s*스택|풀스택|full[-\s]?stack|mern|mevn|스택\s*개발|백엔드\s*및\s*프론트|프론트\s*\+\s*백엔드)",
    "안드로이드 개발자": r"(안드|안드로이드|android|코틀린|kotlin|제트팩|jetpack|컴포즈|compose|android\s*studio)",
    "iOS 개발자": r"(ios|아이오에스|swift|스위프트|objective\s*c|오브젝티브\s*c|swiftui|uikit)",
    "크로스플랫폼 앱개발자": r"(크로스\s*플랫폼|하이브리드|멀티\s*플랫폼|react\s*native|리액트\s*네이티브|flutter|플러터|xamarin|자마린|cordova|코르도바|maui)",
    "게임 클라이언트 개발자": r"(게임\s*클라이언트|게임\s*클라|unity|유니티|언리얼|unreal|cocos|cocos2d|godot|고도트|three\.?js)",
    "게임 서버 개발자": r"(게임\s*서버|game\s*server|mmorpg|매치\s*메이킹|match\s*making|랭킹\s*서버|실시간\s*서버)",
    "DBA": r"(dba|데이터베이스|database|db\s*관리|db\s*운영|db\s*설계|튜닝|성능\s*튜닝|postgres|postgre\s*sql|mysql|mariadb|oracle|mssql|mongodb)",
    "인공지능/머신러닝": r"(인공지능|ai\b|머신\s*러닝|머신러닝|딥\s*러닝|딥러닝|ml\b|pytorch|텐서플로우|tensorflow|트랜스포머|transformer|llm|rag|자연어처리|nlp|컴퓨터\s*비전|cv\b|추천\s*시스템)",
    "DevOps/시스템 엔지니어": r"(데브옵스|devops|플랫폼\s*엔지니어|platform\s*engineer|시스템\s*엔지니어|인프라|infra|sre|ci/?cd|쿠버네티스|kubernetes|k8s|테라폼|terraform|앤서블|ansible|도커|docker|컨테이너|모니터링|prometheus|프로메테우스|grafana|그라파나)",
    "정보보안 담당자": r"(정보\s*보안|보안|security|siem|soc|침해\s*대응|침해|취약점|모의\s*해킹|pentest|포렌식|forensic|red\s*team|blue\s*team|보안\s*관제)",
    "QA 엔지니어": r"(qa\b|품질\s*보증|품질|테스트|테스팅|테스트\s*자동화|automation|테스터|시나리오\s*테스트|selenium|appium|pytest|junit)",
    "개발 PM": r"((?<![a-z])pm(?![a-z])|개발\s*pm|프로젝트\s*매니저|프로덕트\s*매니저|product\s*manager|프로젝트\s*리더|(?<![a-z])pl(?![a-z])|pmo)",
    "HW/임베디드": r"(임베디드|embedded|펌웨어|firmware|하드웨어|hw\b|fpga|rtos|마이컴|mcu|보드|회로|stm32|uart|can|spi)",
    "SW/솔루션": r"(솔루션|sw\s*솔루션|solution|패키지|package|온\s*프레미스|on[-\s]?prem|라이선스|si\s*솔루션)",
    "웹퍼블리셔": r"(웹\s*퍼블리셔|퍼블리셔|퍼블|마크업|markup|html/?css|html|css|웹\s*표준|웹\s*접근성|반응형|시멘틱)",
    "빅데이터 엔지니어": r"(데이터\s*엔지니어|data\s*engineer|데이터\s*파이프라인|분산\s*처리|배치|실시간\s*처리|spark|하둡|hadoop|hive|카프카|kafka|airflow|etl|dbt|snowflake|스노우플레이크|redshift|레드쉬프트|bigquery|빅쿼리|dw\b|데이터\s*웨어하우스)",
    "VR/AR/3D": r"(vr|ar|xr|가상\s*현실|증강\s*현실|혼합\s*현실|3d|유니티|언리얼)",
    "기술지원": r"(기술\s*지원|technical\s*support|고객\s*지원|cs\s*엔지니어|support\s*engineer|운영\s*지원|필드\s*엔지니어|유지\s*보수)",
    "블록체인": r"(블록\s*체인|블록체인|block\s*chain|blockchain|web3|솔리디티|solidity|스마트\s*컨트랙트|smart\s*contract|defi|디파이|nft|지갑|월렛|dapp|디앱)"
}


def industry_bonus(cat, industry_text):
    if not industry_text: return 0
    txt = industry_text.lower()
    b = 0
    if "게임" in industry_text:
        if cat in ("게임 서버 개발자","게임 클라이언트 개발자"):
            b += 4
    if ("전자" in industry_text) or ("반도체" in industry_text):
        if cat in ("HW/임베디드","VR/AR/3D"):
            b += 3
    if ("보안" in industry_text) or ("정보보안" in industry_text):
        if cat == "정보보안 담당자":
            b += 4
    if ("소프트웨어" in industry_text) and (cat in ("서버/백엔드 개발자","프론트엔드 개발자","웹 풀스택 개발자","SW/솔루션")):
        b += 2
    return b

@F.udf("int")
def category_score_udf(cat, title, industry):
    base = dict(base_priority).get(cat, 10)
    s = base
    t = (title or "").lower()
    pat = cat_title_patterns.get(cat)
    if pat and re.search(pat, t, flags=re.IGNORECASE):
        s += 5
    s += industry_bonus(cat, industry or "")
    return int(s)

# ============ 1) 연차 단일값 & 직급(6단계) & 보조컬럼 ============
df1 = (
  spark.createDataFrame(df)
  .withColumn("exp_min", F.col("exp_min").cast("double"))
  .withColumn("exp_max", F.col("exp_max").cast("double"))
  .withColumn("exp_max_adj",
              F.least(F.coalesce(F.col("exp_max"), F.lit(Y_MAX)),
                      F.col("exp_min")+F.lit(CAP_K),
                      F.lit(Y_MAX)))
  .withColumn("span", F.col("exp_max_adj") - F.col("exp_min"))
  .withColumn("alpha", F.when(F.col("span") <= 3.0, F.lit(0.5)).otherwise(F.lit(0.25)))
  .withColumn("y_star", F.col("exp_min") + F.col("alpha")*(F.col("exp_max_adj") - F.col("exp_min")))
  .withColumn("require_experience_single_year",
              F.round(F.greatest(F.lit(0.0), F.least(F.lit(Y_MAX), F.col("y_star")))).cast("int"))
  .withColumn(
      "require_experience_role",
      F.when(F.col("require_experience_single_year")==0, "신입")
       .when((F.col("require_experience_single_year")>=1) & (F.col("require_experience_single_year")<=3), "사원")
       .when((F.col("require_experience_single_year")>=4) & (F.col("require_experience_single_year")<=6), "대리")
       .when((F.col("require_experience_single_year")>=7) & (F.col("require_experience_single_year")<=12), "과장")
       .when((F.col("require_experience_single_year")>=13) & (F.col("require_experience_single_year")<16), "차장") # 13–15
       .when(F.col("require_experience_single_year")>=16, "부장")  # 16 포함
  )
  .withColumn(
      "require_experience_band_kr",
      F.when(F.col("require_experience_single_year")==0, "신입")
       .when((F.col("require_experience_single_year")>=1) & (F.col("require_experience_single_year")<=3), "1-3년")
       .when((F.col("require_experience_single_year")>3) & (F.col("require_experience_single_year")<=5), "3-5년")
       .when((F.col("require_experience_single_year")>5) & (F.col("require_experience_single_year")<=10), "5-10년")
       .otherwise("10년+")
  )
  .withColumn("start_ts", F.to_timestamp("start_datetime", "yyyy.MM.dd HH:mm"))
  .withColumn("posting_start_month_key", F.date_format(F.col("start_ts"), "yyyy-MM"))
  .withColumn("posting_start_date_key", F.date_format(F.col("start_ts"), "yyyy-MM-dd"))
)

# ============ 2) 대표 카테고리: 제목/산업 기반 점수로 1개 선정 ============
post_cat = (
  df1
    .select("posting_id","job_category_kor","posting_title_j","industry")
    .distinct()
    .join(cat_pri_df, on="job_category_kor", how="left")
    .withColumn("base_pri", F.coalesce(F.col("base_pri"), F.lit(10)))
    .withColumn("cat_score", category_score_udf("job_category_kor","posting_title_j","industry"))
)
w = W.partitionBy("posting_id").orderBy(F.desc("cat_score"), F.desc("base_pri"), F.asc("job_category_kor"))
primary_cat = (
  post_cat
    .withColumn("rn", F.row_number().over(w))
    .filter("rn = 1")
    .select("posting_id", F.col("job_category_kor").alias("job_category_kor_one"))
)

# ============ 3) 공고별 카테고리 수(K) → Share 가중치(1/K) ============
k_per_post = (
  df1.select("posting_id","job_category_kor").distinct()
     .groupBy("posting_id").agg(F.count("*").alias("K"))
)

# ============ 4) 기술스택 explode & 중복제거(공고×스택 기준) ============
df_base = (
  df1
  .select("posting_id","exp_min","exp_max",
          "require_experience_single_year","require_experience_role",
          "require_experience_band_kr","posting_start_month_key","posting_start_date_key", "posting_tech_stack")
  .dropDuplicates(["posting_id"])  # 같은 공고 중복행(카테고리별 중복) 제거
)

df_stack = (
  df_base
  .withColumn(
      "posting_tech_stack_one",
      F.explode(
          F.filter(
            F.transform(F.split(F.coalesce(F.col("posting_tech_stack"), F.lit("")), ";"),
                        lambda x: F.trim(x)),
            lambda x: x != ""
          )
      )
  )
  .drop("posting_tech_stack")
)

# 공고×스택 기준 유니크 + 대표카테고리 + K 조인
stack_ready = (
  df_stack
  .join(primary_cat, on="posting_id", how="left")
  .join(k_per_post, on="posting_id", how="left")
  .withColumn("K", F.coalesce(F.col("K"), F.lit(1)))  # 안전장치
  .withColumn("share_w", 1.0 / F.col("K"))
)

# ============ 5) 최종 집계 ============

group_cols = [
  "posting_tech_stack_one",
  "job_category_kor_one",
  "require_experience_single_year",
  "exp_min",
  "exp_max",
  "require_experience_role",
  "require_experience_band_kr",
  "posting_start_month_key",
  "posting_start_date_key"
]

# (a) 중복제거 카운트: 공고 유니크
g_count = (
  stack_ready
  .groupBy(*group_cols)
  .agg(F.countDistinct("posting_id").alias("posting_count_s"))
)

# (b) Share 카운트: 공고별 1/K 가중 합(대표카테고리에 대해 집계)
#    - 같은 공고가 카테고리 여러 개면 1/K만큼만 기여 → 과다계수 방지
g_share = (
  stack_ready
  .select(*group_cols, "posting_id", "share_w")
  .dropDuplicates(["posting_id","posting_tech_stack_one","posting_start_month_key"])  # 공고×스택×월 중복 방어
  .groupBy(*group_cols)
  .agg(F.sum("share_w").alias("posting_share_s"))
)

# (c) 머지 → 최종 테이블
g_final = (
  g_count.join(g_share, on=group_cols, how="left")
)

# 저장 (카탈로그/스키마 쓰면 cat.sch.gld_careerpit_tech_stack_reqs_by_yoe 로 변경)
#g_final.write.format("delta").mode("overwrite").saveAsTable("gld_careerpit_tech_stack_reqs_by_yoe")


In [0]:
g_final.display()

posting_tech_stack_one job_category_kor_one require_experience_single_year exp_min exp_max require_experience_role require_experience_band_kr posting_start_month_key posting_start_date_key posting_count_s posting_share_s Infra 기술지원 12 10.0 20.0 과장 10년+ 2025-08 2025-08-11 1 1.0 ReactQuery 프론트엔드 개발자 6 5.0 10.0 대리 5-10년 2025-08 2025-08-11 1 1.0 MCU HW/임베디드 8 6.0 15.0 과장 5-10년 2025-08 2025-08-13 1 1.0 Slack 인공지능/머신러닝 6 5.0 10.0 대리 5-10년 2025-08 2025-08-13 1 1.0 AWS HW/임베디드 0 0.0 0.0 신입 신입 2025-08 2025-08-15 1 1.0 Kubernetes 웹 풀스택 개발자 3 1.0 10.0 사원 1-3년 2025-08 2025-08-19 1 0.3333333333333333 Photon 게임 클라이언트 개발자 7 5.0 15.0 과장 5-10년 2025-08 2025-08-18 1 0.5 Python SW/솔루션 12 10.0 20.0 과장 10년+ 2025-08 2025-08-18 1 0.5 Python DevOps/시스템 엔지니어 3 1.0 10.0 사원 1-3년 2025-08 2025-08-20 1 1.0 Python SW/솔루션 5 3.0 10.0 대리 3-5년 2025-08 2025-08-20 1 1.0 SpringFramework SW/솔루션 5 3.0 15.0 대리 3-5년 2025-08 2025-08-20 1 0.5 Django 서버/백엔드 개발자 7 6.0 10.0 과장 5-10년 2025-08 2025-08-22 1 1.0 Linux SW/솔루션 6 5.0 10.0 대리 5-10년 2025-08 2025-08-22 1 1.0 Transformers 인공지능/머신러닝 5 3.0 10.0 대리 3-5년 2025-08 2025-08-21 1 1.0 Recoil iOS 개발자 7 5.0 15.0 과장 5-10년 2025-08 2025-08-24 1 0.5 CSS3 웹퍼블리셔 0 0.0 0.0 신입 신입 2025-09 2025-09-01 1 1.0 VisualStudioCode 크로스플랫폼 앱개발자 7 5.0 20.0 과장 5-10년 2025-08 2025-08-25 2 2.0 HW HW/임베디드 4 3.0 7.0 대리 3-5년 2025-08 2025-08-22 1 1.0 jQuery 인공지능/머신러닝 2 1.0 3.0 사원 1-3년 2025-08 2025-08-27 1 1.0 JavaScript 프론트엔드 개발자 6 5.0 10.0 대리 5-10년 2025-08 2025-08-27 1 1.0 Embedded SW/솔루션 3 2.0 4.0 사원 1-3년 2025-08 2025-08-27 1 1.0 C# SW/솔루션 14 13.0 15.0 차장 10년+ 2025-09 2025-09-02 1 0.5 AngularJS 프론트엔드 개발자 6 5.0 10.0 대리 5-10년 2025-09 2025-09-01 1 1.0 Network 기술지원 6 5.0 10.0 대리 5-10년 2025-08 2025-08-29 1 1.0 WhatsApp 기술지원 4 3.0 5.0 대리 3-5년 2025-08 2025-08-29 1 1.0 Shopify 프론트엔드 개발자 5 4.0 6.0 대리 3-5년 2025-08 2025-08-29 1 1.0 CloudFlare DevOps/시스템 엔지니어 4 3.0 5.0 대리 3-5년 2025-09 2025-09-01 1 0.5 C SW/솔루션 3 1.0 10.0 사원 1-3년 2025-09 2025-09-03 4 1.5 SW SW/솔루션 10 9.0 11.0 과장 5-10년 2025-09 2025-09-04 1 1.0 Python 서버/백엔드 개발자 0 0.0 0.0 신입 신입 2025-09 2025-09-04 1 0.5 Yocto HW/임베디드 0 0.0 0.0 신입 신입 2025-09 2025-09-05 1 1.0 AZURE 인공지능/머신러닝 5 3.0 10.0 대리 3-5년 2025-08 2025-08-13 1 0.25 TensorFlow 인공지능/머신러닝 0 0.0 0.0 신입 신입 2025-08 2025-08-12 1 0.3333333333333333 RESTAPI 빅데이터 엔지니어 7 5.0 20.0 과장 5-10년 2025-08 2025-08-12 1 1.0 RESTAPI 서버/백엔드 개발자 6 5.0 10.0 대리 5-10년 2025-08 2025-08-13 1 1.0 AWS 서버/백엔드 개발자 4 2.0 10.0 대리 3-5년 2025-08 2025-08-15 1 1.0 Jasmine 프론트엔드 개발자 4 2.0 10.0 대리 3-5년 2025-08 2025-08-18 1 1.0 Grafana DevOps/시스템 엔지니어 7 5.0 18.0 과장 5-10년 2025-08 2025-08-14 2 1.0 GitLab 프론트엔드 개발자 5 4.0 8.0 대리 3-5년 2025-08 2025-08-16 1 1.0 C SW/솔루션 0 0.0 0.0 신입 신입 2025-08 2025-08-14 1 1.0 PostgreSQL 서버/백엔드 개발자 6 4.0 10.0 대리 5-10년 2025-08 2025-08-18 1 0.5 MySQL 서버/백엔드 개발자 8 6.0 12.0 과장 5-10년 2025-08 2025-08-19 1 1.0 GitHub HW/임베디드 5 3.0 10.0 대리 3-5년 2025-08 2025-08-19 1 1.0 TCP/IP DevOps/시스템 엔지니어 11 10.0 15.0 과장 10년+ 2025-08 2025-08-22 1 0.5 React 서버/백엔드 개발자 7 5.0 12.0 과장 5-10년 2025-08 2025-08-21 1 1.0 Ansible 인공지능/머신러닝 4 2.0 10.0 대리 3-5년 2025-08 2025-08-22 1 0.5 MySQL DBA 7 5.0 15.0 과장 5-10년 2025-08 2025-08-23 1 1.0 Node.js 서버/백엔드 개발자 8 7.0 8.0 과장 5-10년 2025-08 2025-08-27 1 1.0 JSP SW/솔루션 6 4.0 10.0 대리 5-10년 2025-08 2025-08-29 1 1.0 DjangoRESTframework 서버/백엔드 개발자 4 3.0 7.0 대리 3-5년 2025-09 2025-09-01 1 0.5 Node.js 서버/백엔드 개발자 4 3.0 7.0 대리 3-5년 2025-09 2025-09-01 1 0.5 TypeScript 프론트엔드 개발자 8 6.0 9.0 과장 5-10년 2025-08 2025-08-29 2 2.0 jQuery 프론트엔드 개발자 5 4.0 6.0 대리 3-5년 2025-08 2025-08-29 1 1.0 C++ 인공지능/머신러닝 5 4.0 6.0 대리 3-5년 2025-08 2025-08-30 1 1.0 C++ HW/임베디드 2 1.0 3.0 사원 1-3년 2025-09 2025-09-03 1 1.0 Vertica DBA 3 1.0 10.0 사원 1-3년 2025-09 2025-09-01 1 1.0 AWS DevOps/시스템 엔지니어 5 3.0 15.0 대리 3-5년 2025-09 2025-09-01 1 1.0 ISMS DevOps/시스템 엔지니어 4 3.0 5.0 대리 3-5년 2025-09 2025-09-01 1 0.5 AWS DevOps/시스템 엔지니어 11 9.0 15.0 과장 10년+ 2025-09 2025-09-01 1 1.0 JSP 프론트엔드 개발자 5 3.0 15.0 대리 3-5년 2025-09 2025-09-02 1 1.0 Jenkins DBA 4 3.0 8.0 대리 3-5년 2025-09 2025-09-02 1 1.0 Kubeflow DevOps/시스템 엔지니어 9 7.0

In [0]:
# from pyspark.sql import functions as F

# # ----------------------------
# # 1) 단일연차/직급 매핑 컬럼 생성
# # ----------------------------
# CAP_K = 6.0             # 상한 완만 캡(+6년)
# Y_MAX = 20.0

# df1 = (
#   spark.createDataFrame(df)
#   # 안전 캐스팅
#   .withColumn("exp_min", F.col("exp_min").cast("double"))
#   .withColumn("exp_max", F.col("exp_max").cast("double"))
#   # 상한 캡
#   .withColumn("exp_max_adj",
#               F.least(F.coalesce(F.col("exp_max"), F.lit(Y_MAX)),
#                       F.col("exp_min")+F.lit(CAP_K),
#                       F.lit(Y_MAX)))
#   # 폭/알파(좁으면 중앙값 0.5, 넓으면 하한가중 0.25)
#   .withColumn("span", F.col("exp_max_adj") - F.col("exp_min"))
#   .withColumn("alpha", F.when(F.col("span") <= 3.0, F.lit(0.5)).otherwise(F.lit(0.25)))
#   # 단일 연차 실수값 → 0~20, 반올림
#   .withColumn("y_star", F.col("exp_min") + F.col("alpha")*(F.col("exp_max_adj") - F.col("exp_min")))
#   .withColumn("require_experience_single_year",
#               F.round(F.greatest(F.lit(0.0), F.least(F.lit(Y_MAX), F.col("y_star")))).cast("int"))
#   # 요구 직급 라벨(국내 다수결 경계)
#   .withColumn(
#       "require_experience_role",
#       F.when(F.col("require_experience_single_year")==0, "신입")
#        .when((F.col("require_experience_single_year")>=1) & (F.col("require_experience_single_year")<=3), "사원")
#        .when((F.col("require_experience_single_year")>=4) & (F.col("require_experience_single_year")<=6), "대리")
#        .when((F.col("require_experience_single_year")>=7) & (F.col("require_experience_single_year")<=12), "과장")
#        .otherwise("차·부장")
#   )
#   # 국내형 연차 밴드(트렌드 축으로 유용)
#   .withColumn(
#       "require_experience_band_kr",
#       F.when(F.col("require_experience_single_year")==0, "신입")
#        .when((F.col("require_experience_single_year")>=1) & (F.col("require_experience_single_year")<=3), "1-3년")
#        .when((F.col("require_experience_single_year")>3) & (F.col("require_experience_single_year")<=5), "3-5년")
#        .when((F.col("require_experience_single_year")>5) & (F.col("require_experience_single_year")<=10), "5-10년")
#        .otherwise("10년+")
#   )
#   # 공고 시작일 → 월 키(YYYY-MM) (그래프용)
#   .withColumn("start_ts", F.to_timestamp("start_datetime", "yyyy.MM.dd HH:mm"))
#   .withColumn("posting_start_month_key", F.date_format(F.col("start_ts"), "yyyy-MM"))
# )

# # ----------------------------
# # 2) 기술스택 explode (세미콜론 기준)
# # ----------------------------
# df_stack = (
#   df1
#   .withColumn(
#       "posting_tech_stack_one",
#       F.explode(
#           F.filter(
#               F.transform(
#                   F.split(F.coalesce(F.col("posting_tech_stack"), F.lit("")), ";"),
#                   lambda x: F.trim(x)
#               ),
#               lambda x: x != ""
#           )
#       )
#   )
# )

# # ----------------------------
# # 3) 집계: (연차, 직급, 기술스택, 직군, 월) 별 공고 수
# #    - 공고당 중복 방지를 위해 countDistinct(posting_id)
# # ----------------------------
# df_out = (
#   df_stack
#   .groupBy(
#       "require_experience_single_year",
#       "require_experience_role",
#       "posting_tech_stack_one",
#       "job_category_kor",
#       "require_experience_band_kr",
#       "posting_start_month_key"
#   )
#   .agg(F.countDistinct("posting_id").alias("posting_count_s"))
# )

# # ----------------------------
# # 4) 컬럼명 요구사항(오타 대응) + 저장
# # ----------------------------
# # 요청 이름에 'sigle' 오타가 있어 둘 다 제공(원래 single → 별칭 sigle)
# df_final = (
#   df_out
#   .withColumnRenamed("require_experience_single_year", "require_experience_single_year")
#   .withColumnRenamed("require_experience_role", "require_experience_role")
#   .withColumnRenamed("posting_tech_stack_one", "posting_tech_stack_one")
#   .withColumnRenamed("posting_count_s", "posting_count_s")
#   .withColumnRenamed("job_category_kor", "job_category_kor")
# )

# # alias 컬럼(선택): 'sigle' 이름도 필요하면 아래 한 줄 추가
# df_final = df_final.withColumn("require_experience_sigle_year", F.col("require_experience_single_year"))

# # Delta 테이블로 저장 (카탈로그/스키마 쓰면 'cat.sch.gld_careerpit_tech_stack_reqs_by_yoe' 로 바꿔주세요)
# target_table = "gld_careerpit_tech_stack_reqs_by_yoe"
# df_final.write.format("delta").mode("overwrite").saveAsTable(target_table)


- 중복공고 생각 안 하고 굴린 코드

- 초반에 단일 연차 컬럼만 계산하는 코드

In [0]:
# WITH base AS (
#   SELECT
#     exp_min,
#     exp_max,
#     -- 0) 정규화
#     CASE WHEN exp_min IS NULL OR exp_min < 0 THEN 0.0 ELSE exp_min END AS m0,
#     CASE WHEN exp_max IS NULL THEN NULL
#          WHEN exp_max < 0 THEN 0.0
#          ELSE exp_max
#     END AS x0
#   FROM src
# ),
# cap AS (
#   SELECT
#     *,
#     -- 1) 상한 캡
#     LEAST(
#       COALESCE(x0, 20.0),            -- NULL이면 오픈엔드 → 20 가정
#       m0 + 6.0,                      -- CAP_K
#       20.0                           -- Y_MAX
#     ) AS exp_max_adj
#   FROM base
# ),
# span_alpha AS (
#   SELECT
#     *,
#     (exp_max_adj - m0) AS span,
#     CASE WHEN (exp_max_adj - m0) <= 3.0 THEN 0.5 ELSE 0.25 END AS alpha
#   FROM cap
# ),
# ystar AS (
#   SELECT
#     *,
#     (m0 + alpha * (exp_max_adj - m0)) AS y_star
#   FROM span_alpha
# )
# SELECT
#   *,
#   CAST(ROUND(GREATEST(0.0, LEAST(20.0, y_star))) AS INT) AS exp_single_year,
#   CASE
#     WHEN ROUND(GREATEST(0.0, LEAST(20.0, y_star))) = 0 THEN '신입'
#     WHEN ROUND(GREATEST(0.0, LEAST(20.0, y_star))) BETWEEN 1 AND 3 THEN '사원'
#     WHEN ROUND(GREATEST(0.0, LEAST(20.0, y_star))) BETWEEN 4 AND 6 THEN '대리'
#     WHEN ROUND(GREATEST(0.0, LEAST(20.0, y_star))) BETWEEN 7 AND 12 THEN '과장'
#     ELSE '차·부장'
#   END AS kr_grade_majority
# FROM ystar;


---------------------------------------------------------------------------
NameError                                 Traceback (most recent call last)
File <command-8630377583381925>, line 1
----> 1 display(df_final)

NameError: name 'df_final' is not defined

In [0]:
# df_clean = ... # Spark SQL/DSL로 전처리
# df_clean.write.format("delta").mode("overwrite").saveAsTable("catalog.gold.gld_BI_careerpit")

---------------------------------------------------------------------------
NameError                                 Traceback (most recent call last)
File <command-8630377583381925>, line 1
----> 1 display(df_final)

NameError: name 'df_final' is not defined

# 3. 데이터 점검

- 스키마 확인

In [0]:
g_final.printSchema()

root
 |-- posting_tech_stack_one: string (nullable = false)
 |-- job_category_kor_one: string (nullable = true)
 |-- require_experience_single_year: integer (nullable = true)
 |-- exp_min: double (nullable = true)
 |-- exp_max: double (nullable = true)
 |-- require_experience_role: string (nullable = true)
 |-- require_experience_band_kr: string (nullable = false)
 |-- posting_start_month_key: string (nullable = true)
 |-- posting_start_date_key: string (nullable = true)
 |-- posting_count_s: long (nullable = false)
 |-- posting_share_s: double (nullable = true)



- 요약통계 확인

In [0]:
g_final.describe().display()

summary posting_tech_stack_one job_category_kor_one require_experience_single_year exp_min exp_max require_experience_role require_experience_band_kr posting_start_month_key posting_start_date_key posting_count_s posting_share_s count 6336 6336 6336 6336 6336 6336 6336 6336 6336 6336 6336 mean null null 5.800031565656566 4.362215909090909 10.285037878787879 null null null null 1.0874368686868687 0.9314157196969672 stddev null null 3.329038959465098 3.237305106868127 5.422791238198967 null null null null 0.3543750626709099 0.4193610397310223 min .NET DBA 0 0.0 0.0 과장 1-3년 2025-08 2025-08-11 1 0.2 max yolo 프론트엔드 개발자 19 18.0 20.0 차장 신입 2025-09 2025-09-09 7 7.0

- Null 값 확인

In [0]:
from pyspark.sql.functions import col, sum

# 각 컬럼의 null 값 개수 계산
g_final.select([sum(col(c).isNull().cast("int")).alias(c) for c in g_final.columns]).display()

posting_tech_stack_one job_category_kor_one require_experience_single_year exp_min exp_max require_experience_role require_experience_band_kr posting_start_month_key posting_start_date_key posting_count_s posting_share_s 0 0 0 0 0 0 0 0 0 0 0

- 기본키 PK 중복 확인 (사용x)

In [0]:
from pyspark.sql import functions as F

pk = ["posting_tech_stack_one","require_experience_single_year", "job_category_kor_one", "posting_start_month_key",  "posting_start_date_key"]
dupes = (g_final
         .groupBy(*pk).count()
         .filter("count > 1"))
print("중복 PK 수:", dupes.count())
display(dupes)  # 있으면 어떤 키가 겹치는지 확인


중복 PK 수: 194


posting_tech_stack_one require_experience_single_year job_category_kor_one posting_start_month_key posting_start_date_key count JavaScript 4 프론트엔드 개발자 2025-08 2025-08-18 2 Java 10 서버/백엔드 개발자 2025-09 2025-09-04 2 TypeScript 4 서버/백엔드 개발자 2025-08 2025-08-19 2 RESTAPI 4 프론트엔드 개발자 2025-08 2025-08-22 2 Nuxt.js 9 프론트엔드 개발자 2025-09 2025-09-01 2 C++ 5 HW/임베디드 2025-09 2025-09-06 2 Git 6 서버/백엔드 개발자 2025-09 2025-09-06 2 Java 4 서버/백엔드 개발자 2025-09 2025-09-01 2 React 6 프론트엔드 개발자 2025-09 2025-09-01 2 AI/인공지능 5 인공지능/머신러닝 2025-08 2025-08-27 2 JavaScript 6 프론트엔드 개발자 2025-09 2025-09-01 2 Git 2 SW/솔루션 2025-09 2025-09-04 3 C++ 2 HW/임베디드 2025-09 2025-09-03 2 C# 6 SW/솔루션 2025-08 2025-08-29 2 HW 6 HW/임베디드 2025-09 2025-09-01 2 Linux 5 서버/백엔드 개발자 2025-09 2025-09-01 3 C 11 HW/임베디드 2025-09 2025-09-08 2 C# 11 SW/솔루션 2025-09 2025-09-02 2 C++ 3 SW/솔루션 2025-09 2025-09-03 2 Java 6 서버/백엔드 개발자 2025-09 2025-09-01 2 L3 5 기술지원 2025-09 2025-09-01 2 Python 6 DevOps/시스템 엔지니어 2025-09 2025-09-04 2 Linux 7 서버/백엔드 개발자 2025-08 2025-08-14 2 FPGA 5 HW/임베디드 2025-08 2025-08-21 2 Git 6 서버/백엔드 개발자 2025-08 2025-08-18 2 C# 5 SW/솔루션 2025-08 2025-08-11 2 Vue.js 6 프론트엔드 개발자 2025-09 2025-09-01 2 Java 6 서버/백엔드 개발자 2025-09 2025-09-06 2 MySQL 7 서버/백엔드 개발자 2025-08 2025-08-18 2 AZURE 7 DevOps/시스템 엔지니어 2025-09 2025-09-01 2 RESTAPI 4 서버/백엔드 개발자 2025-09 2025-09-01 2 HTML5 4 프론트엔드 개발자 2025-08 2025-08-18 2 EmbeddedLinux 8 SW/솔루션 2025-08 2025-08-13 2 C# 5 SW/솔루션 2025-08 2025-08-25 3 MySQL 6 서버/백엔드 개발자 2025-09 2025-09-06 2 TypeScript 4 프론트엔드 개발자 2025-08 2025-08-31 2 DB 4 서버/백엔드 개발자 2025-08 2025-08-25 2 WPF 5 SW/솔루션 2025-08 2025-08-25 2 RDB 5 서버/백엔드 개발자 2025-09 2025-09-06 2 Java 4 서버/백엔드 개발자 2025-09 2025-09-09 2 Django 3 서버/백엔드 개발자 2025-09 2025-09-03 2 SpringDataJPA 6 서버/백엔드 개발자 2025-09 2025-09-01 2 C 3 SW/솔루션 2025-09 2025-09-04 2 JavaScript 5 SW/솔루션 2025-09 2025-09-02 2 C++ 3 SW/솔루션 2025-08 2025-08-16 2 Java 5 인공지능/머신러닝 2025-08 2025-08-27 2 React 6 프론트엔드 개발자 2025-08 2025-08-18 2 SpringBoot 7 서버/백엔드 개발자 2025-08 2025-08-18 2 VisualStudio 5 SW/솔루션 2025-08 2025-08-11 2 Verilog 6 HW/임베디드 2025-09 2025-09-04 2 Linux 4 SW/솔루션 2025-08 2025-08-13 2 Spring 5 서버/백엔드 개발자 2025-09 2025-09-09 2 Oracle 6 DBA 2025-08 2025-08-31 2 Switch 5 기술지원 2025-09 2025-09-01 2 JavaScript 4 프론트엔드 개발자 2025-08 2025-08-20 2 C# 5 SW/솔루션 2025-09 2025-09-01 2 C 6 HW/임베디드 2025-09 2025-09-04 2 SW 5 SW/솔루션 2025-09 2025-09-01 2 AWS 6 DevOps/시스템 엔지니어 2025-08 2025-08-21 2 MCU 2 HW/임베디드 2025-09 2025-09-03 2 Python 5 인공지능/머신러닝 2025-08 2025-08-22 2 RESTAPI 6 DevOps/시스템 엔지니어 2025-09 2025-09-04 2 C++ 4 SW/솔루션 2025-09 2025-09-04 2 L2 5 기술지원 2025-09 2025-09-01 2 Java 7 SW/솔루션 2025-09 2025-09-01 2 CSS3 4 프론트엔드 개발자 2025-08 2025-08-20 2 C++ 5 SW/솔루션 2025-08 2025-08-27 2 Linux 5 SW/솔루션 2025-08 2025-08-16 2 HTML5 6 프론트엔드 개발자 2025-08 2025-08-18 2 Linux 5 SW/솔루션 2025-09 2025-09-04 2 Java 9 서버/백엔드 개발자 2025-09 2025-09-04 2 React 4 프론트엔드 개발자 2025-08 2025-08-22 3 AWS 6 서버/백엔드 개발자 2025-09 2025-09-02 2 TensorFlow 4 인공지능/머신러닝 2025-08 2025-08-22 2 Java 6 서버/백엔드 개발자 2025-09 2025-09-04 2 AWS 4 서버/백엔드 개발자 2025-08 2025-08-25 2 C# 4 SW/솔루션 2025-09 2025-09-09 2 JavaScript 3 서버/백엔드 개발자 2025-08 2025-08-11 2 SW 4 SW/솔루션 2025-09 2025-09-09 2 Java 6 서버/백엔드 개발자 2025-09 2025-09-02 2 L7 5 기술지원 2025-09 2025-09-01 2 Python 6 서버/백엔드 개발자 2025-09 2025-09-06 2 C++ 4 SW/솔루션 2025-08 2025-08-13 3 SpringBoot 10 서버/백엔드 개발자 2025-09 2025-09-04 2 MySQL 4 서버/백엔드 개발자 2025-09 2025-09-01 3 Git 3 서버/백엔드 개발자 2025-08 2025-08-11 2 Hibernate 6 서버/백엔드 개발자 2025-09 2025-09-01 2 C++ 8 SW/솔루션 2025-08 2025-08-13 3 L4 5 기술지원 2025-09 2025-09-01 2 Vue.js 9 프론트엔드 개발자 2025-09 2025-09-01 2 Docker 6 서버/백엔드 개발자 2025-08 2025-08-18 2 C++ 5 HW/임베디드 2025-08 2025-08-21 2 TypeScript 6 프론트엔드 개발자 2025-09 2025-09-03 2 CSS3 4 프론트엔드 개발자 2025-08 2025-08-22 2 RESTAPI 6 프론트엔드 개발자 2025-08 2025-08-18 2 C 5 서버/백엔드 개발자 2025-09 2025-09-01 2 Network 5 기술지원 2025-09 2025-09-01 3 WPF 4 SW/솔루션 2025-09 2025-09-09 2 Python 3 SW/솔루션 2025-08 2025-08-16 2 Node.js 4 서버/백엔드 개발자 2025-09 2025-09-01 2 MCU 5 HW/임베디드 2025-08 2025-08-21 2 Linux 2 

# 4. DB 저장

- 타입확인

In [0]:
# pyspark.sql.dataframe.DataFrame
type(g_final)

---------------------------------------------------------------------------
NameError                                 Traceback (most recent call last)
File <command-8630377583381925>, line 1
----> 1 display(df_final)

NameError: name 'df_final' is not defined

%md
- 적재

In [0]:
# ===== 파라미터 =====
jdbcHostname = "cloud-postgredb-server.postgres.database.azure.com"
jdbcPort     = 5432
jdbcDatabase = "postgres"          # 생성해둔 DB 이름
targetTable  = "gold.gld_employee_careerpit_tech_stack_reqs" # 스키마.테이블

jdbc_user     = "Drawbridge" #Administrator login 정보
jdbc_pass = "asdASD123!@#"
# 보안 권장: Databricks Secret 사용(예시는 평문 대체)
# pgPassword = dbutils.secrets.get(scope="prod", key="pg-password")

# SSL 필요
jdbcUrl = f"jdbc:postgresql://{jdbcHostname}:{jdbcPort}/{jdbcDatabase}?sslmode=require"


# ===== 적재(append/overwrite 택1) =====
(
  g_final.write
    .format("jdbc")
    .option("url", jdbcUrl)
    .option("dbtable", targetTable)
    .option("user", jdbc_user)
    .option("password", jdbc_pass)
    .option("driver", "org.postgresql.Driver")
    # 선택: 성능/동작 옵션
    # .option("batchsize", "10000")      # 대량 적재 시
    .option("truncate", "true")      # mode("overwrite")와 함께 사용 시 테이블 구조 유지 후 TRUNCATE
    .mode("overwrite")                    # 또는 "append"
    .save()
)
